In [415]:
from pandas_datareader import data as web
import os
import numpy as np
import pandas as pd
import plotly.graph_objects as go
import torch
import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader

In [416]:
# Stock market indices
# assets = ['^GSPC', '^DJI', '^IXIC', '^RUT']

assets = ['SPY', 'DIA', 'ONEQ', 'IWM']

asset_list = assets

In [417]:
# Iterate through index list, check if we already have the data (load it) or go get it from Yahoo! (save it)
# Make a dictionary of dataframes containing all the data

start_date = '01-01-2005'
stop_date = '05-01-2018'
directory = '../../../data/yahoo_data'

# If the 'directory' doesn't exist, create it
if os.path.isdir(directory) == False:
    os.mkdir(directory)

asset_dict = {}

for asset in asset_list:
    pathname = directory + '/' + asset + '_' + start_date + '.csv'
    if os.path.isfile(pathname) == True:
        print('Loading from file: ', pathname)        
        df = pd.read_csv(pathname, index_col='Date')
    else:
        print('Downloading from Yahoo! - ', asset)
        df = web.DataReader(asset, data_source='yahoo', start=start_date, end=stop_date)
        df.to_csv(pathname)    

    # Just before we put it in the dictionary, copy the index to a Date field and make a new index which enumerates
    # all the entries.
    df.insert(0, 'Date', df.index)
    df.index = np.arange(df.shape[0])
    df['Date']=pd.to_datetime(df['Date'], format='%Y/%m/%d')
    
    asset_dict[asset] = df 

Loading from file:  ../../../data/yahoo_data/SPY_01-01-2005.csv
Loading from file:  ../../../data/yahoo_data/DIA_01-01-2005.csv
Loading from file:  ../../../data/yahoo_data/ONEQ_01-01-2005.csv
Loading from file:  ../../../data/yahoo_data/IWM_01-01-2005.csv


In [418]:
for asset in asset_list:
    display(asset_dict[asset].head(5))
    print(asset, asset_dict[asset].describe())

Date        High         Low        Open       Close      Volume  \
0 2005-01-03  121.760002  119.900002  121.559998  120.300003  55748000.0   
1 2005-01-04  120.540001  118.440002  120.459999  118.830002  69167600.0   
2 2005-01-05  119.250000  118.000000  118.739998  118.010002  65667300.0   
3 2005-01-06  119.150002  118.260002  118.440002  118.610001  47814700.0   
4 2005-01-07  119.230003  118.129997  118.970001  118.440002  55847700.0   

   Adj Close  
0  87.421600  
1  86.353340  
2  85.757454  
3  86.193451  
4  86.069946

SPY               High          Low         Open        Close        Volume  \
count  3355.000000  3355.000000  3355.000000  3355.000000  3.355000e+03   
mean    158.618683   156.850125   157.777961   157.785174  1.480847e+08   
std      47.267962    47.257414    47.268697    47.273572  1.009376e+08   
min      70.000000    67.099998    67.949997    68.110001  1.527000e+07   
25%     124.024998   122.645000   123.509998   123.364998  7.687135e+07   
50%     141.869995   140.380005   141.160004   141.190002  1.196369e+08   
75%     199.370003   197.560005   198.470001   198.644997  1.860118e+08   
max     286.630005   284.500000   285.929993   286.579987  8.710263e+08   

         Adj Close  
count  3355.000000  
mean    133.794391  
std      50.344772  
min      53.503864  
25%      94.983700  
50%     112.221672  
75%     176.385826  
max     270.951447  


Date        High         Low        Open       Close      Volume  \
0 2005-01-03  108.589996  106.930000  108.150002  107.320000  11691300.0   
1 2005-01-04  107.599998  105.889999  107.500000  106.300003  10628300.0   
2 2005-01-05  106.779999  105.709999  106.300003  105.709999  10885300.0   
3 2005-01-06  106.660004  105.830002  106.129997  106.040001   8238900.0   
4 2005-01-07  106.500000  105.629997  106.330002  105.839996   8555700.0   

   Adj Close  
0  73.506165  
1  72.807533  
2  72.403397  
3  72.629478  
4  72.492485

DIA               High          Low         Open        Close        Volume  \
count  3355.000000  3355.000000  3355.000000  3355.000000  3.355000e+03   
mean    141.717285   140.264581   141.021648   141.029833  9.071673e+06   
std      40.051009    39.990225    40.029948    40.023839  8.081543e+06   
min      67.169998    64.779999    65.510002    65.440002  1.006800e+06   
25%     111.160004   109.685001   110.279999   110.400002  4.433950e+06   
50%     129.460007   128.000000   128.820007   128.800003  6.657000e+06   
75%     170.584999   169.260002   169.889999   170.020004  1.030350e+07   
max     265.929993   264.119995   265.559998   265.910004  9.169520e+07   

         Adj Close  
count  3355.000000  
mean    116.519076  
std      43.828723  
min      49.443554  
25%      81.676556  
50%      99.338135  
75%     147.937439  
max     249.256119  


Date       High        Low       Open      Close    Volume  Adj Close
0 2005-01-03  86.449997  84.730003  86.250000  84.910004   40300.0  73.121384
1 2005-01-04  85.489998  82.839996  85.489998  83.250000   68800.0  71.691879
2 2005-01-05  83.480003  82.500000  83.339996  82.540001  112800.0  71.080414
3 2005-01-06  83.019997  82.339996  82.419998  82.449997   38300.0  71.002930
4 2005-01-07  82.930000  81.870003  82.400002  82.400002   38300.0  70.959862

ONEQ               High          Low         Open        Close        Volume  \
count  3355.000000  3355.000000  3355.000000  3355.000000  3.355000e+03   
mean    134.788319   133.137759   134.124319   133.999705  4.808244e+04   
std      57.932287    57.563535    57.831186    57.771240  1.506505e+05   
min      51.750000    49.500000    50.230000    49.799999  8.000000e+02   
25%      90.505001    89.160004    90.000000    89.800003  9.500000e+03   
50%     109.260002   108.000000   108.709999   108.650002  1.740000e+04   
75%     182.885002   179.529999   181.714996   181.320000  3.250000e+04   
max     299.750000   296.820007   299.250000   297.859985  2.490400e+06   

         Adj Close  
count  3355.000000  
mean    123.096690  
std      57.440780  
min      44.096684  
25%      78.924301  
50%      97.158524  
75%     170.002983  
max     286.494904  


Date       High        Low       Open      Close      Volume  \
0 2005-01-03  65.209999  63.570000  65.095001  63.910000  16062600.0   
1 2005-01-04  64.084999  62.430000  64.035004  62.540001  27450000.0   
2 2005-01-05  62.639999  61.290001  62.470001  61.290001  29884200.0   
3 2005-01-06  62.200001  61.224998  61.669998  61.615002  23061200.0   
4 2005-01-07  61.950001  60.895000  61.755001  60.930000  20906200.0   

   Adj Close  
0  51.335308  
1  50.234875  
2  49.230827  
3  49.491879  
4  48.941639

IWM               High          Low         Open        Close        Volume  \
count  3355.000000  3355.000000  3355.000000  3355.000000  3.355000e+03   
mean     90.878000    89.442976    90.204790    90.202952  4.973638e+07   
std      28.328728    28.271442    28.302914    28.304778  3.133952e+07   
min      35.639999    34.259998    34.730000    34.389999  5.060000e+04   
25%      69.939999    68.225002    69.174999    69.165001  2.836570e+07   
50%      81.150002    79.910004    80.570000    80.620003  4.178410e+07   
75%     115.150002   113.645000   114.405003   114.430000  6.193485e+07   
max     160.630005   158.770004   160.360001   159.960007  3.551170e+08   

         Adj Close  
count  3355.000000  
mean     80.354959  
std      29.464536  
min      29.028275  
25%      57.749250  
50%      69.029083  
75%     105.353165  
max     153.777161  


In [419]:
# Display a Plotly interactive candelstick chart

def plotly_candlestick(asset_dict, asset_name):

    df = asset_dict[asset_name]
    
    trace1 = {
        'x': df.Date,
        'open': df.Open,
        'close': df.Close,
        'high': df.High,
        'low': df.Low,
        'type': 'candlestick',
        'name': asset_name,
        'showlegend': True
    }

    data = [trace1]
        
    layout = go.Layout({
        'title': {
            'text': 'Asset: ' + asset_name,
            'font': {
                'size': 20
            }
        }
    })

    fig = go.Figure(trace1, layout)
    fig.show()

# Plot all the assets in Plotly interactive charts with a Candlestick chart
for asset in asset_list:
    plotly_candlestick(asset_dict, asset)

In [420]:
# Before we split the data into train, validation and test sets let's add the Prev Adj Close feature and
# remove the Date and Volume columns (which are not used)

for asset in asset_list:
    # Add a feature called Prev Adj CLose
    prev_adj_close = asset_dict[asset]['Adj Close'].shift(1).copy()
    asset_dict[asset]['Prev Adj Close'] = prev_adj_close

    # Take care of special case of very first previous Adj close - just make is the same as the Adj Close
    asset_dict[asset]['Prev Adj Close'][0] = asset_dict[asset]['Prev Adj Close'][1]

    # Round the number of decimal places to 3
    asset_dict[asset] = asset_dict[asset].round(3)
    
    # Volume isn't used
    asset_dict[asset] = asset_dict[asset].drop(columns=['Volume'])
       
    display(asset, asset_dict[asset].head(5))

C:\Users\q2\Anaconda3\envs\mlp\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



'SPY'

Date    High     Low    Open   Close  Adj Close  Prev Adj Close
0 2005-01-03  121.76  119.90  121.56  120.30     87.422          87.422
1 2005-01-04  120.54  118.44  120.46  118.83     86.353          87.422
2 2005-01-05  119.25  118.00  118.74  118.01     85.757          86.353
3 2005-01-06  119.15  118.26  118.44  118.61     86.193          85.757
4 2005-01-07  119.23  118.13  118.97  118.44     86.070          86.193

C:\Users\q2\Anaconda3\envs\mlp\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



'DIA'

...

'ONEQ'

Date   High    Low   Open  Close  Adj Close  Prev Adj Close
0 2005-01-03  86.45  84.73  86.25  84.91     73.121          73.121
1 2005-01-04  85.49  82.84  85.49  83.25     71.692          73.121
2 2005-01-05  83.48  82.50  83.34  82.54     71.080          71.692
3 2005-01-06  83.02  82.34  82.42  82.45     71.003          71.080
4 2005-01-07  82.93  81.87  82.40  82.40     70.960          71.003

C:\Users\q2\Anaconda3\envs\mlp\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



'IWM'

Date    High     Low    Open   Close  Adj Close  Prev Adj Close
0 2005-01-03  65.210  63.570  65.095  63.910     51.335          51.335
1 2005-01-04  64.085  62.430  64.035  62.540     50.235          51.335
2 2005-01-05  62.640  61.290  62.470  61.290     49.231          50.235
3 2005-01-06  62.200  61.225  61.670  61.615     49.492          49.231
4 2005-01-07  61.950  60.895  61.755  60.930     48.942          49.492

In [421]:
# Define the start and end dates for each of the sets - start and end dates are inclusive

train_start = '01-01-2005'
train_end = '01-01-2008'
valid_start = '01-02-2008'
valid_end = '12-31-2009'
test_start = '01-01-2010'
test_end = '05-01-2018'
train_val_start = '01-01-2005'
train_val_end = '12-31-2009'

In [422]:
paper_baseline = {'SPY':136.4, 'DIA':136.6, 'ONEQ':228.9, 'IWM':163.5}

train_asset_dict = {}
valid_asset_dict = {}
test_asset_dict = {}
train_val_asset_dict = {}

print('Asset\tBeg$\tEnd$\tGain%\tPaper%')
for asset in asset_list:
    # Make a dataframe for this asset
    df = asset_dict[asset]
    
    # Mask off the training data and assign result to a train_asset dictionary
    mask = (df['Date'] >= train_start) & (df['Date'] <= train_end)
    train_asset_dict[asset] = df.loc[mask]
    
    # Mask off the validation data and assign result to a valid_asset dictionary
    mask = (df['Date'] >= valid_start) & (df['Date'] <= valid_end)
    valid_asset_dict[asset] = df.loc[mask]
    
    # Mask off the test data and assign result to a test_asset dictionary
    mask = (df['Date'] >= test_start) & (df['Date'] <= test_end)
    test_asset_dict[asset] = df.loc[mask]
    
    # Mask off the test data and assign result to a test_asset dictionary
    mask = (df['Date'] >= train_val_start) & (df['Date'] <= train_val_end)
    train_val_asset_dict[asset] = df.loc[mask]

    # Reset the indices to start from 0 again for each of the dataframes
    train_asset_dict[asset].index = np.arange(train_asset_dict[asset].shape[0])    
    valid_asset_dict[asset].index = np.arange(valid_asset_dict[asset].shape[0])    
    test_asset_dict[asset].index = np.arange(test_asset_dict[asset].shape[0])
    train_val_asset_dict[asset].index = np.arange(train_val_asset_dict[asset].shape[0])    

    
#    display(test_asset_dict[asset])
    
    # Print the buy and hold returns over the entire test period (the papers baseline)
    start = test_asset_dict[asset]['Adj Close'].loc[0]
    end = test_asset_dict[asset]['Adj Close'].loc[test_asset_dict[asset].shape[0]-1]
    gain = 100.0 * (end - start) / start
    
    print(asset, '\t{:1.2f}'.format(start), '\t{:1.2f}'.format(end), '\t{:1.2f}'.format(gain), '\t{:1.2f}'.format(paper_baseline[asset]))


Asset	Beg$	End$	Gain%	Paper%
SPY 	91.09 	251.53 	176.15 	136.40
DIA 	81.86 	226.79 	177.04 	136.60
ONEQ 	81.00 	269.47 	232.68 	228.90
IWM 	54.72 	148.46 	171.30 	163.50


In [423]:
print(len(train_asset_dict['SPY']))
print(len(valid_asset_dict['SPY']))
print(len(test_asset_dict['SPY']))

754
505
2096


In [424]:
# This will normalise each column of a dataframe - currently not being used
def normalize(df):
    result = df.copy()
    for feature_name in df.columns:
        max_value = df[feature_name].max()
        min_value = df[feature_name].min()
        result[feature_name] = (df[feature_name] - min_value) / (max_value - min_value)
    return result

In [425]:
# Given one of the asset train, valid or test dataframes, this will make a new three dimensional list which has
# dimensions (num_samples, window_size - tw, 6) which represents the effect of sliding a window of width window_size (tw)
# down the dataframe from start to end and collecting the input features into a length 6 vector.  This will be our
# input dataset to the LSTM.

# In addition, also generate a list of (training) labels which is "tomorrow's" adjusted closing price - the thing 
# we are trying to predict. There is a single training label for each tw x 6 set of inputs.


def create_input_sequences_from_df(input_data_df, tw):
    in_seq = []
    out_seq= []
    L = len(input_data_df)

    for i in range(L-tw):
        seq = []
        for j in range(tw):
            features = [input_data_df['Open'].loc[i+j], input_data_df['Low'].loc[i+j], input_data_df['High'].loc[i+j], 
                        input_data_df['Close'].loc[i+j], 
                         input_data_df['Prev Adj Close'].loc[i+j], input_data_df['Adj Close'].loc[i+j]]
            seq.append(features)

        train_label = input_data_df['Adj Close'].loc[i+tw]
        out_seq.append(train_label)
        in_seq.append(seq)
    return in_seq, out_seq


In [426]:
# Let's generate the SPY training set

df = train_asset_dict['SPY']
display(df.head(5))

train_window = 22
train_seq, train_labels = create_input_sequences_from_df(df, train_window)
# print(train_inout_seq)

# Convert our list of lists to Tensors
train_seq = torch.FloatTensor(train_seq)
train_labels = torch.FloatTensor(train_labels)

print(train_seq.shape)
print(train_labels.shape)

# Print first couple of entries to check 
print(train_seq[0])
print(train_labels[0])

print(train_seq[1])
print(train_labels[1])

Date    High     Low    Open   Close  Adj Close  Prev Adj Close
0 2005-01-03  121.76  119.90  121.56  120.30     87.422          87.422
1 2005-01-04  120.54  118.44  120.46  118.83     86.353          87.422
2 2005-01-05  119.25  118.00  118.74  118.01     85.757          86.353
3 2005-01-06  119.15  118.26  118.44  118.61     86.193          85.757
4 2005-01-07  119.23  118.13  118.97  118.44     86.070          86.193

torch.Size([732, 22, 6])
torch.Size([732])
tensor([[121.5600, 119.9000, 121.7600, 120.3000,  87.4220,  87.4220],
        [120.4600, 118.4400, 120.5400, 118.8300,  87.4220,  86.3530],
        [118.7400, 118.0000, 119.2500, 118.0100,  86.3530,  85.7570],
        [118.4400, 118.2600, 119.1500, 118.6100,  85.7570,  86.1930],
        [118.9700, 118.1300, 119.2300, 118.4400,  86.1930,  86.0700],
        [118.3400, 118.3400, 119.4600, 119.0000,  86.0700,  86.4770],
        [118.6400, 117.9900, 118.7400, 118.1800,  86.4770,  85.8810],
        [118.4000, 117.5200, 118.8400, 118.5700,  85.8810,  86.1640],
        [118.6400, 117.5000, 118.7300, 117.6200,  86.1640,  85.4740],
        [117.9700, 117.7600, 118.5300, 118.2400,  85.4740,  85.9250],
        [118.0500, 117.9500, 119.6200, 119.4700,  85.9250,  86.8180],
        [119.4300, 118.2100, 119.5200, 118.2200,  86.8180,  85.9100],
        [117.8900, 117.2900, 118.2000, 117.5000,  85.9100,  85.3870],
        [117.7900, 116.6500, 118.0000, 116.7800

In [427]:
# Let's generate the SPY VALIDATION set

df = valid_asset_dict['SPY']
display(df.head(5))

train_window = 22
valid_seq, valid_labels = create_input_sequences_from_df(df, train_window)
# print(train_inout_seq)

# Convert our list of lists to Tensors
valid_seq = torch.FloatTensor(valid_seq)
valid_labels = torch.FloatTensor(valid_labels)

print(valid_seq.shape)
print(valid_labels.shape)

# Print first couple of entries to check 
print(valid_seq[0])
print(valid_labels[0])

print(valid_seq[1])
print(valid_labels[1])


Date    High     Low    Open   Close  Adj Close  Prev Adj Close
0 2008-01-02  146.99  143.88  146.53  144.93    111.174         112.156
1 2008-01-03  145.49  144.07  144.91  144.86    111.120         111.174
2 2008-01-04  143.44  140.91  143.34  141.31    108.397         111.120
3 2008-01-07  142.23  140.10  141.81  141.19    108.305         108.397
4 2008-01-08  142.90  138.44  142.08  138.91    106.556         108.305

torch.Size([483, 22, 6])
torch.Size([483])
tensor([[146.5300, 143.8800, 146.9900, 144.9300, 112.1560, 111.1740],
        [144.9100, 144.0700, 145.4900, 144.8600, 111.1740, 111.1200],
        [143.3400, 140.9100, 143.4400, 141.3100, 111.1200, 108.3970],
        [141.8100, 140.1000, 142.2300, 141.1900, 108.3970, 108.3050],
        [142.0800, 138.4400, 142.9000, 138.9100, 108.3050, 106.5560],
        [139.0900, 137.7000, 140.7900, 140.3700, 106.5560, 107.6760],
        [139.6800, 139.3700, 142.8000, 141.2900, 107.6760, 108.3820],
        [140.7800, 139.0000, 141.9000, 140.1500, 108.3820, 107.5070],
        [141.1600, 140.4000, 141.8600, 141.2800, 107.5070, 108.3740],
        [139.7900, 137.9000, 141.4900, 138.1700, 108.3740, 105.9880],
        [137.3600, 136.2800, 139.1200, 136.9800, 105.9880, 105.0760],
        [137.8100, 132.9300, 137.8800, 133.4300, 105.0760, 102.3520],
        [134.7400, 131.1000, 135.0200, 132.0600, 102.3520, 101.3020],
        [127.2100, 126.0000, 132.4300, 130.7200

In [433]:
# torch.cuda.is_available() checks and returns a Boolean True if a GPU is available, else it'll return False
is_cuda = torch.cuda.is_available()

print("Cuda available:",torch.cuda.is_available())

# If we have a GPU available, we'll set our device to GPU. We'll use this device variable later in our code.
if is_cuda:
    device = torch.device("cuda")
else:
    device = torch.device("cpu")
    
device = torch.device("cpu")    


Cuda available: True


In [787]:
# Modified From stack abuse tutorial
# Note this is not yet the Chalvatzis architecture as this is a many to one implementation,
# not a many to many as he used in his paper.

class NeilLSTM(nn.Module):
    def __init__(self, input_size = 6, hidden_layer_size = 64, output_size = 1, n_layers = 3, dropout=0.5):
        super().__init__()
        
        # Store some dimensions we need to know in the forward pass
        self.n_layers = n_layers        
        self.hidden_layer_size = hidden_layer_size

        # Define the LSTM layer
        self.lstm = nn.LSTM(input_size, hidden_layer_size, n_layers, 
                            batch_first=False, bias=False, dropout=dropout, bidirectional=False)
        
#        torch.nn.init.xavier_uniform(self.lstm.weight)

        # Create two tensors in order to do a dummy forward pass to get the right output size for the fc layer
        # lstm_out, hidden self.lstm( input_seq.view( len(input_seq) , 1 , -1), hidden)
#        weight = next(self.parameters()).data
        
#        print("weight:", weight.shape)
#        hidden = weight.new(self.n_layers, batch_size, self.hidden_layer_size).zero_()
#        hidden = torch.zeros(22, 64)
#        print("hidden shape:", hidden.shape)
        
        # Define the linear layer
        # Perhaps should perform forward on the lstm to explicitly get the size of the 
        # tensor for sequence to one vs sequence to sequence versions.
        
        # The size of the linear layer for LH model 
        self.linear = nn.Linear(hidden_layer_size, output_size, bias = True)
        
        torch.nn.init.xavier_uniform_(self.linear.weight)        
        
        
#        self.linear = nn.Linear(64 * 22, output_size)

        
    # Forward pass
    # input_seq shape is: (sequence length, num input features) - there's no batch dimension
    def forward(self, input_seq, hidden, verbose=0):
        # o, h = lstm(i, h)
        # input_seq.view( len(input_seq) , 1 , -1) converts the input_seq 2D tensor to a 3D tensor
        # with dimensions: seq length, 1, num input features
        # I think this is to make it compatible with what the forward pass of lstm expects
        # which is: (seq_len, batch, input_size).  Our batch is always 1

        if verbose:
            print("\n\nlstm input:\n", input_seq)
            print("\n\nlstm input view:\n", input_seq.view( len(input_seq) , 1 , -1))
            print("\n\nlstm hidden input:\n", hidden)
        lstm_out, hidden = self.lstm( input_seq.view( len(input_seq) , 1 , -1), hidden)
        if verbose:
            print("\n\nlstm_output:\n", lstm_out)
            print("\n\nhidden output:\n", hidden)
            
        
        # Feed forward the outputs of the lstm into the linear layer       
        # lstm_out dims are (seq_len, batch, hidden dim)
        # This is converted to (seq_len, hidden_dim) before input to the linear layer
        
#        print(lstm_out.shape)
#        print(lstm_out.view(len(input_seq), -1).shape)

        # When T=22 and hidden_layer_size=64, the shape of the lstm_out tensor is [22,1,64]    
        # This view reshapes it to [22, 64]
        lstm_out_view = lstm_out.view(len(input_seq), -1)
        if verbose:
            print("\n\nlstm_out_view:\n", lstm_out_view)
        
#        lstm_out_view = lstm_out.view(-1)
#        print(lstm_out_view.shape)
        
#        torch.set_printoptions(threshold = 10000)
#        print(lstm_out_view)
#        print(lstm_out_view[-1])
        
        # Just present the last hidden state to the linear network
        if verbose:
            print("\n\nLinear weights:\n", self.linear.weight)
            print("\n\ninput to fc:\n", lstm_out_view[-1])
        predictions = self.linear(lstm_out_view[-1])

    
#        predictions = self.linear(lstm_out_view[0])
#        predictions = self.linear(lstm_out_view)

        if verbose:
            print("\n\npredictions:\n",predictions)
        
        # predictions has dimension: (seq_len, 1)
        # We return the last value and the hidden / cell layers
        
#        return predictions[-1], hidden
        return predictions, hidden
    
    def init_hidden(self, batch_size = 1):
        weight = next(self.parameters()).data
        hidden = (weight.new(self.n_layers, batch_size, self.hidden_layer_size).zero_().to(device),
                 weight.new(self.n_layers, batch_size, self.hidden_layer_size).zero_().to(device))
        return(hidden)
        

In [788]:
from timeit import default_timer as timer

def create_train_model2(train_seq, train_labels, train_start, train_length, epochs = 20, num_layers = 3, hidden_size = 64, dropout=0.5, lr = 0.001, dr=0.999, verbosity=0):
    input_size = 6
    lr_decay_rate = dr

    if verbosity>=1:
        print("Building LSTM Model with the following parameters:")
        print("Num layers:", num_layers)
        print("Hidden size:", hidden_size)
        print("Dropout:", dropout)
        print("Learning Rate:", lr)
        print("Start training...")
    
    model = NeilLSTM(input_size, hidden_size, output_size, num_layers, dropout)
    model.to(device)

    loss_function = nn.MSELoss()

    optimizer = torch.optim.Adam(model.parameters(), lr=lr)
    my_lr_scheduler = torch.optim.lr_scheduler.ExponentialLR(optimizer = optimizer, gamma = lr_decay_rate)
    
    batch_size = 1  # batch mode isn't used actually but including for future possible use
    
    start_time = timer()
        
    # This might need to be inside the training loop
    h = model.init_hidden(batch_size)  
   
    if verbosity>=2:
        print(train_seq[train_start])
        print(train_labels[train_start])
        
        print(train_seq[train_start+1])
        print(train_labels[train_start+1])
        
        print('Epoch\tTrLoss\t\tTAdjC\tTPred\tTAct\tPredRt\tActRt\tValLoss\t\tVAdjC\tVPred\tVAct\tVPredRt\tVActRt')            
                

    min_valid_loss = 1E32
    min_valid_idx = -1
    min_valid_train_loss = -1
            
    # Per section 4.1 Chalvatzis
    for i in range(epochs):
        j = train_start

        # Send input / label data to Cuda if available
        inputs = train_seq[j].to(device)
        labels = train_labels[j].to(device)
        
        model.train()
        
        # Initialise hidden states before every epoch
        h = model.init_hidden(batch_size)  
                            
        # This is needed inside the sequence loop for back propagation to work (possibly only for cuda)
        h = tuple(e.data for e in h)
        
        optimizer.zero_grad()
        
        if i==1599:
            y_pred, h = model(inputs, h, verbose=1)
        else:
            y_pred, h = model(inputs, h, verbose=0)
               
        # y_pred returns all T values of the output layer, we just want the last one (LH)
        train_loss = loss_function(y_pred[-1], labels)
               
        # Compute gradients and update the model
        train_loss.backward()
        optimizer.step()
        my_lr_scheduler.step()
                       
        # Compute metrics for the training set
        training_loss = train_loss.item()
        train_adj_close = inputs[-1][-1].item()
        train_pred = y_pred[-1].item()
        train_truth = labels.item()
        train_predicted_return = (train_pred / train_adj_close) - 1            
        train_actual_return = (train_truth / train_adj_close) - 1

        # Compute metrics for the validation
        model.eval()
        j = train_start + 1
            
        inputs = train_seq[j].to(device)
        labels = train_labels[j].to(device)
            
        with torch.no_grad():
            h = model.init_hidden(batch_size)
        
            y_pred, h = model(inputs, h)
            valid_adj_close = inputs[-1][-1].item()                
            valid_pred = y_pred[-1].item()
            valid_truth = labels.item()
            valid_loss = (valid_pred - valid_truth)**2
                
#                print(y_pred.item(), labels.item(), y_pred.item() - labels.item(), (y_pred.item() - labels.item())**2)
            
            valid_predicted_return = (valid_pred / valid_adj_close) - 1
            valid_actual_return = (valid_truth / valid_adj_close) - 1
            
            # Keep track of the best validation point
            if valid_loss < min_valid_loss:
                min_valid_loss = valid_loss
                min_valid_idx = i
                min_valid_train_loss = training_loss           

            if verbosity>=2:
                print('{:3}'.format(i), '\t{:4.5e}'.format(training_loss),
                     '\t{:2.3f}'.format(train_adj_close), 
                     '\t{:2.3f}'.format(train_pred), '\t{:2.3f}'.format(train_truth),
                      '\t{:2.3f}'.format(train_predicted_return), '\t{:2.3f}'.format(train_actual_return),
                      '\t{:4.5e}'.format(valid_loss), '\t{:2.3f}'.format(valid_adj_close), 
                      '\t{:2.3f}'.format(valid_pred), '\t{:2.3f}'.format(valid_truth),
                      '\t{:2.3f}'.format(valid_predicted_return), '\t{:2.3f}'.format(valid_actual_return))                    
        
    if verbosity>=1:
        print("Done! Training time:{:1.2f}".format(timer()-start_time))
        
    # Validation - How well can we predict the next sample after training the model fully on the training set
    model.eval()

    # Set input to the very next sample in the train / validation set (after training)               
    inputs = train_seq[train_start+1].to(device)
    labels = train_labels[train_start+1].to(device)
    
    with torch.no_grad():
        h = model.init_hidden(batch_size)
 
        y_pred, h = model(inputs, h, verbose=0)
#        y_pred, h = model(inputs, h, verbose=1)
                
        err = (y_pred.item() - labels.item())**2
            
        predicted_return = (y_pred.item() / inputs[-1][-1].item()) - 1
        actual_return = (labels.item() / inputs[-1][-1].item()) - 1
        
        if verbosity>=1:
            print('VLoss\t\tAdjC\t\tPred\t\tAct\t\tPredRt\t\tActRt')    
            print('{:4.5e}'.format(err),
                 '\t{:2.4f}'.format(inputs[-1][-1].item()), 
                 '\t{:2.4f}'.format(y_pred.item()), '\t{:2.4f}'.format(labels.item()),
                  '\t{:2.3e}'.format(predicted_return), '\t{:2.3e}'.format(actual_return))
            
            print('Min Valid Loss:{:2.3e}'.format(min_valid_loss), 'Min Valid Epoch:', 
                  min_valid_idx, 'Min Valid Training Loss:{:2.3e}'.format(min_valid_train_loss))
          
    result_dict = {'PReturn':predicted_return, 'AReturn':actual_return, 'MinValLoss': min_valid_loss, 'MinValIdx':min_valid_idx, 'MinValTrainLoss':min_valid_train_loss}
    
    return result_dict



In [789]:
import csv

def run_hypers(window_size = 22, asset='SPY', epochs=20, num_layers=3, hidden_size=64, dropout=0.5, lr=0.001, dr=0.999, verbosity=0):

    train_window = window_size

    # Generate training set
    df = train_asset_dict[asset]

    train_seq, train_labels = create_input_sequences_from_df(df, train_window)

    # Convert our list of lists to Tensors
    train_seq = torch.FloatTensor(train_seq)
    train_labels = torch.FloatTensor(train_labels)

    # Generate validation set
    df = valid_asset_dict[asset]

    valid_seq, valid_labels = create_input_sequences_from_df(df, train_window)

    # Convert our list of lists to Tensors
    valid_seq = torch.FloatTensor(valid_seq)
    valid_labels = torch.FloatTensor(valid_labels)
    
    # Generate training / validation set
    df = train_val_asset_dict[asset]

    train_val_seq, train_val_labels = create_input_sequences_from_df(df, train_window)

    # Convert our list of lists to Tensors
    train_val_seq = torch.FloatTensor(train_val_seq)
    train_val_labels = torch.FloatTensor(train_val_labels)
    

    if verbosity>=1:
        print("Running hyper-parameter experiment:")
        print("Window size:", window_size)
        print("Training set:", train_seq.size())
        print("Validation set:", valid_seq.size())    
        print("Training / Validation set:", train_val_seq.size())
    
    # Now run the model
    
    # Stop one short of the end as we use the t+1 for validation

    predicted_returns = []
    actual_returns = []
    
#    for i in range(len(train_seq) - 1):    
    for i in range(1):
        print("\nSequence:", i)
        result_dict = create_train_model2(train_seq, train_labels, 0, len(train_labels), epochs=epochs, num_layers=num_layers, hidden_size=hidden_size, dropout=dropout, lr=lr, dr=dr, verbosity=verbosity)
        predicted_returns.append(result_dict['PReturn'])
        actual_returns.append(result_dict['AReturn'])       
    
        with open("ch5_log.csv", 'a', newline='') as myfile:
            wr = csv.writer(myfile, quoting=csv.QUOTE_ALL)
            wr.writerow((i,result_dict['PReturn'],result_dict['AReturn']))

    result_dict = {'PReturns':predicted_returns, 'AReturns':actual_returns}
    
    return result_dict

In [793]:
torch.set_printoptions(threshold=10000)
# These are Chalvatzis LH optimal hyper settings
result_dict = run_hypers(window_size = 11, asset='SPY', epochs=1600, num_layers=3, hidden_size=128, dropout=0.5, lr=0.002, dr=1, verbosity=2)

Running hyper-parameter experiment:
Window size: 11
Training set: torch.Size([743, 11, 6])
Validation set: torch.Size([494, 11, 6])
Training / Validation set: torch.Size([1248, 11, 6])

Sequence: 0
Building LSTM Model with the following parameters:
Num layers: 3
Hidden size: 128
Dropout: 0.5
Learning Rate: 0.002
Start training...
tensor([[121.5600, 119.9000, 121.7600, 120.3000,  87.4220,  87.4220],
        [120.4600, 118.4400, 120.5400, 118.8300,  87.4220,  86.3530],
        [118.7400, 118.0000, 119.2500, 118.0100,  86.3530,  85.7570],
        [118.4400, 118.2600, 119.1500, 118.6100,  85.7570,  86.1930],
        [118.9700, 118.1300, 119.2300, 118.4400,  86.1930,  86.0700],
        [118.3400, 118.3400, 119.4600, 119.0000,  86.0700,  86.4770],
        [118.6400, 117.9900, 118.7400, 118.1800,  86.4770,  85.8810],
        [118.4000, 117.5200, 118.8400, 118.5700,  85.8810,  86.1640],
        [118.6400, 117.5000, 118.7300, 117.6200,  86.1640,  85.4740],
        [117.9700, 117.7600, 118.5300,

 65 	3.26271e+03 	86.818 	28.790 	85.910 	-0.668 	-0.010 	3.17533e+03 	85.910 	29.037 	85.387 	-0.662 	-0.006
 66 	3.23485e+03 	86.818 	29.034 	85.910 	-0.666 	-0.010 	3.14787e+03 	85.910 	29.281 	85.387 	-0.659 	-0.006
 67 	3.20701e+03 	86.818 	29.280 	85.910 	-0.663 	-0.010 	3.12061e+03 	85.910 	29.525 	85.387 	-0.656 	-0.006
 68 	3.17981e+03 	86.818 	29.520 	85.910 	-0.660 	-0.010 	3.09357e+03 	85.910 	29.767 	85.387 	-0.654 	-0.006
 69 	3.15192e+03 	86.818 	29.768 	85.910 	-0.657 	-0.010 	3.06673e+03 	85.910 	30.009 	85.387 	-0.651 	-0.006
 70 	3.12477e+03 	86.818 	30.010 	85.910 	-0.654 	-0.010 	3.04009e+03 	85.910 	30.250 	85.387 	-0.648 	-0.006
 71 	3.09811e+03 	86.818 	30.249 	85.910 	-0.652 	-0.010 	3.01365e+03 	85.910 	30.490 	85.387 	-0.645 	-0.006
 72 	3.07157e+03 	86.818 	30.488 	85.910 	-0.649 	-0.010 	2.98742e+03 	85.910 	30.730 	85.387 	-0.642 	-0.006
 73 	3.04509e+03 	86.818 	30.728 	85.910 	-0.646 	-0.010 	2.96138e+03 	85.910 	30.968 	85.387 	-0.640 	-0.006
 74 	3.019

145 	1.57801e+03 	86.818 	46.186 	85.910 	-0.468 	-0.010 	1.52121e+03 	85.910 	46.384 	85.387 	-0.460 	-0.006
146 	1.56239e+03 	86.818 	46.383 	85.910 	-0.466 	-0.010 	1.50632e+03 	85.910 	46.576 	85.387 	-0.458 	-0.006
147 	1.54711e+03 	86.818 	46.577 	85.910 	-0.464 	-0.010 	1.49154e+03 	85.910 	46.767 	85.387 	-0.456 	-0.006
148 	1.53216e+03 	86.818 	46.767 	85.910 	-0.461 	-0.010 	1.47689e+03 	85.910 	46.957 	85.387 	-0.453 	-0.006
149 	1.51739e+03 	86.818 	46.956 	85.910 	-0.459 	-0.010 	1.46235e+03 	85.910 	47.146 	85.387 	-0.451 	-0.006
150 	1.50276e+03 	86.818 	47.145 	85.910 	-0.457 	-0.010 	1.44792e+03 	85.910 	47.335 	85.387 	-0.449 	-0.006
151 	1.48797e+03 	86.818 	47.336 	85.910 	-0.455 	-0.010 	1.43362e+03 	85.910 	47.524 	85.387 	-0.447 	-0.006
152 	1.47355e+03 	86.818 	47.523 	85.910 	-0.453 	-0.010 	1.41943e+03 	85.910 	47.712 	85.387 	-0.445 	-0.006
153 	1.45910e+03 	86.818 	47.712 	85.910 	-0.450 	-0.010 	1.40535e+03 	85.910 	47.899 	85.387 	-0.442 	-0.006
154 	1.445

227 	6.70653e+02 	86.818 	60.013 	85.910 	-0.309 	-0.010 	6.36614e+02 	85.910 	60.156 	85.387 	-0.300 	-0.006
228 	6.63289e+02 	86.818 	60.156 	85.910 	-0.307 	-0.010 	6.29346e+02 	85.910 	60.300 	85.387 	-0.298 	-0.006
229 	6.55728e+02 	86.818 	60.303 	85.910 	-0.305 	-0.010 	6.22147e+02 	85.910 	60.444 	85.387 	-0.296 	-0.006
230 	6.48513e+02 	86.818 	60.444 	85.910 	-0.304 	-0.010 	6.15017e+02 	85.910 	60.587 	85.387 	-0.295 	-0.006
231 	6.41465e+02 	86.818 	60.583 	85.910 	-0.302 	-0.010 	6.07955e+02 	85.910 	60.730 	85.387 	-0.293 	-0.006
232 	6.33985e+02 	86.818 	60.731 	85.910 	-0.300 	-0.010 	6.00961e+02 	85.910 	60.872 	85.387 	-0.291 	-0.006
233 	6.26963e+02 	86.818 	60.871 	85.910 	-0.299 	-0.010 	5.94035e+02 	85.910 	61.014 	85.387 	-0.290 	-0.006
234 	6.19901e+02 	86.818 	61.012 	85.910 	-0.297 	-0.010 	5.87175e+02 	85.910 	61.155 	85.387 	-0.288 	-0.006
235 	6.12777e+02 	86.818 	61.156 	85.910 	-0.296 	-0.010 	5.80381e+02 	85.910 	61.296 	85.387 	-0.287 	-0.006
236 	6.058

311 	2.42750e+02 	86.818 	70.330 	85.910 	-0.190 	-0.010 	2.23728e+02 	85.910 	70.429 	85.387 	-0.180 	-0.006
312 	2.39641e+02 	86.818 	70.430 	85.910 	-0.189 	-0.010 	2.20729e+02 	85.910 	70.530 	85.387 	-0.179 	-0.006
313 	2.36554e+02 	86.818 	70.530 	85.910 	-0.188 	-0.010 	2.17765e+02 	85.910 	70.630 	85.387 	-0.178 	-0.006
314 	2.33634e+02 	86.818 	70.625 	85.910 	-0.187 	-0.010 	2.14835e+02 	85.910 	70.730 	85.387 	-0.177 	-0.006
315 	2.30419e+02 	86.818 	70.730 	85.910 	-0.185 	-0.010 	2.11938e+02 	85.910 	70.829 	85.387 	-0.176 	-0.006
316 	2.27500e+02 	86.818 	70.827 	85.910 	-0.184 	-0.010 	2.09075e+02 	85.910 	70.928 	85.387 	-0.174 	-0.006
317 	2.24538e+02 	86.818 	70.925 	85.910 	-0.183 	-0.010 	2.06245e+02 	85.910 	71.026 	85.387 	-0.173 	-0.006
318 	2.21537e+02 	86.818 	71.026 	85.910 	-0.182 	-0.010 	2.03449e+02 	85.910 	71.123 	85.387 	-0.172 	-0.006
319 	2.18596e+02 	86.818 	71.125 	85.910 	-0.181 	-0.010 	2.00685e+02 	85.910 	71.221 	85.387 	-0.171 	-0.006
320 	2.157

...

1295 	1.58470e-06 	86.818 	85.911 	85.910 	-0.010 	-0.010 	2.74266e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1296 	5.82077e-07 	86.818 	85.911 	85.910 	-0.010 	-0.010 	2.74266e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1297 	4.56348e-06 	86.818 	85.908 	85.910 	-0.010 	-0.010 	2.74266e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1298 	4.56348e-08 	86.818 	85.910 	85.910 	-0.010 	-0.010 	2.74266e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1299 	4.71482e-09 	86.818 	85.910 	85.910 	-0.010 	-0.010 	2.74266e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1300 	6.72881e-08 	86.818 	85.910 	85.910 	-0.010 	-0.010 	2.74266e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1301 	2.32831e-08 	86.818 	85.910 	85.910 	-0.010 	-0.010 	2.74266e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1302 	8.85339e-06 	86.818 	85.907 	85.910 	-0.010 	-0.010 	2.74266e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1303 	3.35276e-06 	86.818 	85.912 	85.910 	-0.010 	-0.010 	2.74266e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1304 	2.28

1378 	1.04518e-06 	86.818 	85.911 	85.910 	-0.010 	-0.010 	2.74123e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1379 	1.97068e-06 	86.818 	85.911 	85.910 	-0.010 	-0.010 	2.74147e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1380 	3.63274e-07 	86.818 	85.911 	85.910 	-0.010 	-0.010 	2.74155e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1381 	1.71625e-05 	86.818 	85.906 	85.910 	-0.011 	-0.010 	2.74171e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1382 	7.46013e-06 	86.818 	85.907 	85.910 	-0.010 	-0.010 	2.74187e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1383 	6.78934e-07 	86.818 	85.911 	85.910 	-0.010 	-0.010 	2.74195e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1384 	1.24075e-06 	86.818 	85.911 	85.910 	-0.010 	-0.010 	2.74210e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1385 	5.06552e-06 	86.818 	85.912 	85.910 	-0.010 	-0.010 	2.74218e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1386 	9.17405e-06 	86.818 	85.907 	85.910 	-0.010 	-0.010 	2.74226e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1387 	9.31

1464 	1.30967e-06 	86.818 	85.911 	85.910 	-0.010 	-0.010 	2.74378e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1465 	1.25781e-06 	86.818 	85.909 	85.910 	-0.010 	-0.010 	2.74378e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1466 	4.30504e-07 	86.818 	85.911 	85.910 	-0.010 	-0.010 	2.74370e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1467 	2.66568e-06 	86.818 	85.908 	85.910 	-0.010 	-0.010 	2.74362e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1468 	3.38076e-06 	86.818 	85.912 	85.910 	-0.010 	-0.010 	2.74346e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1469 	5.82077e-09 	86.818 	85.910 	85.910 	-0.010 	-0.010 	2.74346e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1470 	5.23869e-10 	86.818 	85.910 	85.910 	-0.010 	-0.010 	2.74338e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1471 	1.74210e-06 	86.818 	85.911 	85.910 	-0.010 	-0.010 	2.74330e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1472 	5.66617e-06 	86.818 	85.912 	85.910 	-0.010 	-0.010 	2.74314e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1473 	9.38

1546 	5.14323e-07 	86.818 	85.911 	85.910 	-0.010 	-0.010 	2.74163e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1547 	1.02190e-05 	86.818 	85.907 	85.910 	-0.010 	-0.010 	2.74163e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1548 	1.41654e-06 	86.818 	85.909 	85.910 	-0.010 	-0.010 	2.74171e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1549 	1.01421e-06 	86.818 	85.909 	85.910 	-0.010 	-0.010 	2.74179e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1550 	9.40659e-06 	86.818 	85.907 	85.910 	-0.010 	-0.010 	2.74195e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1551 	6.78934e-07 	86.818 	85.911 	85.910 	-0.010 	-0.010 	2.74203e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1552 	5.23869e-08 	86.818 	85.910 	85.910 	-0.010 	-0.010 	2.74218e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1553 	3.27418e-07 	86.818 	85.911 	85.910 	-0.010 	-0.010 	2.74218e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1554 	3.93484e-08 	86.818 	85.910 	85.910 	-0.010 	-0.010 	2.74226e-01 	85.910 	85.911 	85.387 	0.000 	-0.006
1555 	7.96

 Parameter containing:
tensor([[ 0.6519,  0.7492,  0.6793,  0.6834, -0.7615,  0.7270, -0.6913,  0.6397,
         -0.6080, -0.5747, -0.6505, -0.7803,  0.7213,  0.5600,  0.6473,  0.6827,
          0.6006,  0.7175,  0.6773, -0.7665,  0.7815, -0.6556,  0.6570, -0.0131,
         -0.5848, -0.7894, -0.7759,  0.6790, -0.7400,  0.6635, -0.7646, -0.6624,
          0.7795,  0.7292,  0.6260, -0.5888, -0.0028,  0.6770,  0.7177, -0.7155,
          0.6739, -0.6883, -0.7147,  0.7404,  0.7164,  0.0096,  0.6365, -0.7211,
          0.6892,  0.7398, -0.6567, -0.7256, -0.6865, -0.7265,  0.7848, -0.6893,
         -0.7210,  0.6384, -0.6309,  0.7223, -0.7850, -0.7647, -0.7234,  0.6089,
          0.7080,  0.3021, -0.7375,  0.7345,  0.7617,  0.7565, -0.6045, -0.7888,
         -0.6602, -0.6461,  0.7139,  0.6665,  0.6268,  0.6789,  0.0013,  0.6525,
         -0.7527, -0.7337,  0.5793,  0.7455,  0.7216,  0.5727, -0.6308,  0.6388,
         -0.7061,  0.7793, -0.7371, -0.8030, -0.6467,  0.6210,  0.6818,  0.7952,
     

In [ ]:
# IGNORE EVERYTHING BELOW HERE

In [301]:
score = run_hypers(window_size = 199, asset='SPY', epochs=30, num_layers=3, hidden_size=8, dropout=0.5, verbose=True)

Running hyper-parameter experiment:
Window size: 199
Training set: torch.Size([555, 199, 6])
Validation set: torch.Size([306, 199, 6])
Building LSTM Model with the following parameters:
Num layers: 3
Hidden size: 8
Dropout: 0.5
Epoch	T_Loss	Train	Agree	UpDays	PredUp		Valid	Agree	UpDays	PredUp
  0 	11033.5 	10015.2 	43.604 	56.036 	0.000 		4614.0 	45.098 	54.902 	0.000
  1 	9996.1 	8899.7 	43.604 	56.036 	0.000 		3956.6 	45.098 	54.902 	0.000
  2 	9052.6 	7995.8 	43.604 	56.036 	0.000 		3378.1 	45.098 	54.902 	0.000
  3 	8178.9 	7169.7 	43.604 	56.036 	0.000 		2859.6 	45.098 	54.902 	0.000
  4 	7362.9 	6405.7 	43.604 	56.036 	0.000 		2393.8 	45.098 	54.902 	0.000
  5 	6601.9 	5696.8 	43.604 	56.036 	0.000 		1976.6 	45.098 	54.902 	0.000
  6 	5891.3 	5038.5 	43.604 	56.036 	0.000 		1605.4 	45.098 	54.902 	0.000
  7 	5228.2 	4428.4 	43.604 	56.036 	0.000 		1278.1 	45.098 	54.902 	0.000
  8 	4611.4 	3864.4 	43.604 	56.036 	0.000 		993.3 	45.098 	54.902 	0.000
  9 	4039.6 	3345.1 	43.604 	5

{'best_epoch_model': NeilLSTM(
   (lstm): LSTM(6, 8, num_layers=3, dropout=0.5)
   (linear): Linear(in_features=8, out_features=1, bias=True)
 ),
 'epoch': 20,
 'valid_loss': 360.6730958246077,
 'agree_pct': 54.90196078431372,
 'up_days_pct': 54.90196078431372,
 'loss_vs_epoch': [(0, 11033.548828125, 4614.0251602016715, 45.09803921568628),
  (1, 9996.146484375, 3956.6178662452717, 45.09803921568628),
  (2, 9052.62890625, 3378.091685210579, 45.09803921568628),
  (3, 8178.89306640625, 2859.589425490247, 45.09803921568628),
  (4, 7362.86328125, 2393.7966875496127, 45.09803921568628),
  (5, 6601.8798828125, 1976.6142633778356, 45.09803921568628),
  (6, 5891.2666015625, 1605.351508649616, 45.09803921568628),
  (7, 5228.24609375, 1278.076614418353, 45.09803921568628),
  (8, 4611.36669921875, 993.2881336711919, 45.09803921568628),
  (9, 4039.584228515625, 749.7129101255517, 45.09803921568628),
  (10, 3511.370849609375, 546.1796925826619, 45.09803921568628),
  (11, 3026.34912109375, 381.518951

In [264]:
# This is for doing randomised trials over the hyper-parameters

import random
import pickle
verbose = True

results = []
if not verbose:
    print('Trial\tEpoch\tV_loss\tAgree%\tWindow\tLayers\tHidden\tDropout')

for trial in range(100):
    if verbose:
        print("Trial:", trial)
    hidden_size = random.choice((8,16,32,64,128))
    num_layers = random.choice((1,2,3,4,5))
    window_size = random.randrange(5,200)
#    print(hidden_size, num_layers, window_size)

    result = run_hypers(window_size = window_size, asset='SPY', epochs=50, num_layers=num_layers, hidden_size=hidden_size, dropout=0.5, verbose=verbose)
    
    result['Trial'] = trial
    results.append(result)
    
    result_str = str(trial) + ',' + str(result['epoch']) + ',' + '{:1.2f}'.format(result['valid_loss']) + ',' + '{:1.2f}'.format(result['agree_pct']) + ',' + '{:1.2f}'.format(result['up_days_pct']) + ',' + str(result['window']) + ',' + str(result['num_layers']) + ',' + str(result['hidden_size']) + ',' + str(result['dropout']) + '\n'
        
    print(trial, result['epoch'], '{:1.2f}'.format(result['valid_loss']), '{:1.2f}'.format(result['agree_pct']), 
          '{:1.2f}'.format(result['up_days_pct']), result['window'], result['num_layers'], result['hidden_size'], result['dropout'])

    with open("trial_results.csv","a") as f:
        f.write(result_str)
          
        
    filename = 'result' + str(trial) + '.pkl'
    with open(filename , 'wb') as f:
        pickle.dump(result, f, pickle.HIGHEST_PROTOCOL)


Trial: 0
Running hyper-parameter experiment:
Window size: 132
Training set: torch.Size([622, 132, 6])
Validation set: torch.Size([373, 132, 6])
Building LSTM Model with the following parameters:
Num layers: 5
Hidden size: 16
Dropout: 0.5
Epoch	Train Loss	Valid Loss	Pct Agree	Pct Up Days
  0 	9721.19 	4289.14 	45.968 	54.301
  1 	7822.88 	3083.23 	45.968 	54.301
  2 	6228.05 	2141.36 	45.968 	54.301
  3 	4882.19 	1413.18 	45.968 	54.301
  4 	3749.35 	870.49 	45.968 	54.301
  5 	2807.74 	491.88 	46.774 	54.301
  6 	2039.86 	258.26 	50.269 	54.301
  7 	1430.02 	150.31 	48.387 	54.301
  8 	962.68 	146.56 	49.462 	54.301
  9 	620.89 	221.99 	51.613 	54.301
 10 	385.36 	347.50 	53.226 	54.301
 11 	234.60 	491.30 	54.839 	54.301
 12 	145.89 	623.72 	55.108 	54.301
 13 	97.85 	724.98 	54.301 	54.301
 14 	73.57 	790.48 	54.301 	54.301
 15 	61.80 	827.61 	54.301 	54.301
 16 	56.18 	846.99 	54.301 	54.301
 17 	53.48 	856.78 	54.301 	54.301
 18 	52.14 	861.71 	54.301 	54.301
 19 	94.30 	734.67 	54

 45 	1.57 	1594.00 	54.037 	54.037
 46 	1.02 	1569.36 	54.037 	54.037
 47 	9.90 	1247.05 	54.037 	54.037
 48 	11.25 	1235.71 	54.037 	54.037
 49 	9.60 	1232.83 	54.037 	54.037
3 10 281.58 55.28 54.04 182 5 16 0.5
Trial: 4
Running hyper-parameter experiment:
Window size: 140
Training set: torch.Size([614, 140, 6])
Validation set: torch.Size([365, 140, 6])
Building LSTM Model with the following parameters:
Num layers: 5
Hidden size: 16
Dropout: 0.5
Epoch	Train Loss	Valid Loss	Pct Agree	Pct Up Days
  0 	9679.87 	4204.20 	46.154 	54.121
  1 	7813.15 	3031.10 	46.154 	54.121
  2 	6243.69 	2109.30 	46.154 	54.121
  3 	4911.20 	1394.54 	46.154 	54.121
  4 	3787.68 	860.45 	46.154 	54.121
  5 	2849.16 	486.64 	46.978 	54.121
  6 	2081.57 	254.80 	49.725 	54.121
  7 	1468.99 	146.43 	48.352 	54.121
  8 	996.49 	141.06 	50.000 	54.121
  9 	647.98 	214.87 	51.374 	54.121
 10 	405.15 	340.12 	53.297 	54.121
 11 	247.51 	486.18 	55.220 	54.121
 12 	153.21 	623.67 	55.220 	54.121
 13 	101.27 	731.65

 40 	51.21 	1017.43 	54.902 	54.902
 41 	51.22 	1017.40 	54.902 	54.902
 42 	51.22 	1017.38 	54.902 	54.902
 43 	51.22 	1017.37 	54.902 	54.902
 44 	51.23 	1017.36 	54.902 	54.902
 45 	51.23 	1017.36 	54.902 	54.902
 46 	51.23 	1017.36 	54.902 	54.902
 47 	51.23 	1017.35 	54.902 	54.902
 48 	51.23 	1017.35 	54.902 	54.902
 49 	51.23 	1017.35 	54.902 	54.902
7 20 359.73 54.90 54.90 198 2 8 0.5
Trial: 8
Running hyper-parameter experiment:
Window size: 13
Training set: torch.Size([741, 13, 6])
Validation set: torch.Size([492, 13, 6])
Building LSTM Model with the following parameters:
Num layers: 4
Hidden size: 32
Dropout: 0.5
Epoch	Train Loss	Valid Loss	Pct Agree	Pct Up Days
  0 	6667.85 	3125.27 	46.436 	53.768
  1 	3748.64 	1345.51 	46.436 	53.768
  2 	1943.21 	494.89 	49.491 	53.768
  3 	913.67 	236.86 	49.287 	53.768
  4 	397.95 	293.38 	51.731 	53.768
  5 	177.60 	441.65 	54.786 	53.768
  6 	94.93 	558.47 	53.360 	53.768
  7 	71.86 	605.88 	53.564 	53.768
  8 	64.62 	623.12 	54.175 	

 37 	2.01 	1095.33 	53.441 	53.441
 38 	8.06 	1092.13 	53.441 	53.441
 39 	1.47 	1029.91 	53.441 	53.441
 40 	2.66 	1092.82 	53.441 	53.441
 41 	3.83 	1095.91 	53.441 	53.441
 42 	2.42 	1090.93 	53.441 	53.441
 43 	1.67 	1078.23 	53.441 	53.441
 44 	0.50 	1047.84 	53.441 	53.441
 45 	0.07 	988.32 	53.441 	53.441
 46 	0.00 	988.25 	53.441 	53.441
 47 	0.32 	1032.10 	53.441 	53.441
 48 	2.18 	1081.93 	53.441 	53.441
 49 	1.74 	1069.80 	53.441 	53.441
11 3 619.07 54.25 53.44 10 3 64 0.5
Trial: 12
Running hyper-parameter experiment:
Window size: 33
Training set: torch.Size([721, 33, 6])
Validation set: torch.Size([472, 33, 6])
Building LSTM Model with the following parameters:
Num layers: 4
Hidden size: 32
Dropout: 0.5
Epoch	Train Loss	Valid Loss	Pct Agree	Pct Up Days
  0 	6874.61 	3168.35 	46.497 	53.715
  1 	3952.87 	1395.22 	46.497 	53.715
  2 	2106.28 	521.88 	48.408 	53.715
  3 	1022.17 	235.68 	49.682 	53.715
  4 	456.59 	277.67 	52.017 	53.715
  5 	202.77 	432.21 	53.928 	53.715
  6

 32 	43.59 	1031.60 	54.232 	54.232
 33 	48.62 	1008.93 	54.232 	54.232
 34 	51.54 	996.44 	54.232 	54.232
 35 	52.48 	992.50 	54.232 	54.232
 36 	51.53 	996.48 	54.232 	54.232
 37 	48.65 	1008.88 	54.232 	54.232
 38 	51.50 	996.63 	54.232 	54.232
 39 	53.17 	989.67 	54.232 	54.232
 40 	54.16 	985.62 	54.232 	54.232
 41 	54.73 	983.28 	54.232 	54.232
 42 	55.06 	981.97 	54.232 	54.232
 43 	55.24 	981.20 	54.232 	54.232
 44 	55.35 	980.77 	54.232 	54.232
 45 	55.42 	980.51 	54.232 	54.232
 46 	55.46 	980.35 	54.232 	54.232
 47 	55.48 	980.26 	54.232 	54.232
 48 	55.49 	980.20 	54.232 	54.232
 49 	55.50 	980.17 	54.232 	54.232
15 20 406.90 54.23 54.23 185 5 8 0.5
Trial: 16
Running hyper-parameter experiment:
Window size: 145
Training set: torch.Size([609, 145, 6])
Validation set: torch.Size([360, 145, 6])
Building LSTM Model with the following parameters:
Num layers: 5
Hidden size: 64
Dropout: 0.5
Epoch	Train Loss	Valid Loss	Pct Agree	Pct Up Days
  0 	4611.46 	1219.78 	45.961 	54.318
  1

KeyboardInterrupt: 

In [73]:
input_size = 6
hidden_size = 64
output_size = 1
num_layers = 3

model = NeilLSTM(input_size, hidden_size, output_size, num_layers)
model.to(device)

loss_function = nn.MSELoss()

optimizer = torch.optim.Adam(model.parameters(), lr=0.001)

epochs = 20

batch_size = 1  # batch mode isn't used actually but including for future possible use

train_loss_vs_epoch = []

# Put the model in training mode (vs model.eval() mode - validation)
model.train()

for i in range(epochs):

    h = model.init_hidden(batch_size)
    model.train()
    
    # Iterate through each of the training samples (seq_len x features)
    for j in range(len(train_labels)):

        # At begining of each training samples we zero out the hidden and cell states
        # This seems a bit odd to me. In the Floydhub example,the hidden / cell states are reset at the 
        # beginning of each epoch.
        # Hidden and cell state dimensions should be num layers x batch size x hidden layer size
            
        # This is needed inside the sequence loop for back propagation to work
        h = tuple(e.data for e in h)

        # Send input / label data to Cuda if available
        inputs = train_seq[j].to(device)
        labels = train_labels[j].to(device)
        
        optimizer.zero_grad()
            
        y_pred, h = model(inputs, h)
               
        # y_pred returns all T values of the output layer, we just want the last one (LH)
        train_loss = loss_function(y_pred[-1], labels)
#        print(y_pred)
 
        # Printing out the training loss etc during one of the later epoch's reveals that even when the eventual
        # epoch loss is close to zero, at the start of each epoch the loss is quite high. It gets down to zero
        # perhaps after 200 or so of the training samples. So, even with a trained network, you need to train the 
        # LSTM with a sequence of training samples to get the loss down first. I think this must be what folks
        # refer to as "warming up" the network.
#        if i == 0:
#            print(i, j, y_pred, labels.item(), train_loss.item())
               
        train_loss.backward()
        optimizer.step()
        
    # Measure the validation loss

    model.eval()
    err = 0
#    h = model.init_hidden(batch_size)
    for j in range(len(valid_labels)):
#        print(j)
        inputs = valid_seq[j].to(device)
#        print(inputs)
        labels = valid_labels[j].to(device)
#        print(labels)
        
#        optimizer.zero_grad()

        with torch.no_grad():
            h = model.init_hidden(batch_size)
#            print("h:",h)
            y_pred, h = model(inputs, h)
#            print("y_pred:", y_pred)
#            print("h:", h)
            
#        print(y_pred.item())
#        print(labels.item())
        err = err + (y_pred.item() - labels.item())**2
    
    valid_loss = err / len(valid_labels)
        
#            print(j, y_pred[0].data, valid_labels[j])
        
#        train_loss = loss_function(y_pred, labels)
    

    print('Epoch:{:3}'.format(i), '\tTrain Loss:{:1.3f}'.format(train_loss.item()), '\tValid Loss:{:1.3f}'.format(valid_loss))
    train_loss_vs_epoch.append((i, train_loss.item()))

print('Epoch:{:3}'.format(i), '\tTrain Loss:{:1.3f}'.format(train_loss.item()), '\tValid Loss:{:1.3f}'.format(valid_loss))    


Epoch:  0 	Train Loss:3809.507 	Valid Loss:1349.974
Epoch:  1 	Train Loss:1042.572 	Valid Loss:244.944
Epoch:  2 	Train Loss:245.258 	Valid Loss:385.710
Epoch:  3 	Train Loss:73.659 	Valid Loss:613.167
Epoch:  4 	Train Loss:34.386 	Valid Loss:727.175


KeyboardInterrupt: 

In [19]:
print(y_pred)
print(labels)

tensor([87.8790], device='cuda:0', grad_fn=<SelectBackward>)
tensor(86.2180, device='cuda:0')


In [23]:
trace1 = {
    'x': np.array(train_loss_vs_epoch)[:,0],
    'y': np.array(train_loss_vs_epoch)[:,1],
    'type': 'scatter',
#    'name': 'Training',
    'showlegend': False
}

data = [trace1]
        
layout = go.Layout({
    'title': {
        'text': 'Training Loss vs Epoch',
        'font': {
            'size': 20
        }
    }
})

fig = go.Figure(trace1, layout)
fig.show()


In [34]:
df = valid_asset_dict['SPY']
display(df.head(5))

train_window = 22
valid_seq, valid_labels = create_input_sequences_from_df(df, train_window)
# print(train_inout_seq)

# Convert our list of lists to Tensors
valid_seq = torch.FloatTensor(valid_seq)
valid_labels = torch.FloatTensor(valid_labels)

h = model.init_hidden(batch_size)
    
results = []    
# Iterate through each of the training samples (seq_len x features)
# for j in range(len(train_labels)):
for j in range(len(valid_labels)):

        # At begining of each training samples we zero out the hidden and cell states
        # This seems a bit odd to me. In the Floydhub example,the hidden / cell states are reset at the 
        # beginning of each epoch.
        # Hidden and cell state dimensions should be num layers x batch size x hidden layer size
            
        # This is needed inside the sequence loop for back propagation to work
    h = tuple(e.data for e in h)

        # Send input / label data to Cuda if available
#    inputs = train_seq[j].to(device)
#    labels = train_labels[j].to(device)
        
    inputs = valid_seq[j].to(device)
    labels = valid_labels[j].to(device)
        
    optimizer.zero_grad()
            
    y_pred, h = model(inputs, h)
       
    train_loss = loss_function(y_pred, labels)
 
        # Printing out the training loss etc during one of the later epoch's reveals that even when the eventual
        # epoch loss is close to zero, at the start of each epoch the loss is quite high. It gets down to zero
        # perhaps after 200 or so of the training samples. So, even with a trained network, you need to train the 
        # LSTM with a sequence of training samples to get the loss down first. I think this must be what folks
        # refer to as "warming up" the network.  Not sure.

    print(i, j, y_pred[0].item(), labels.item(), train_loss.item())
    results.append((j, y_pred[0].item(), labels.item(), train_loss.item()))
    
               
    train_loss.backward()
    optimizer.step()
        
    # Measure the validation loss
valid_loss = 0
    

print('Epoch:{:3}'.format(i), '\tTrain Loss:{:1.3f}'.format(train_loss.item()), '\tValid Loss:{:1.3f}'.format(valid_loss))


Date    High     Low    Open   Close  Adj Close  Prev Adj Close
0 2008-01-02  146.99  143.88  146.53  144.93    111.174         112.156
1 2008-01-03  145.49  144.07  144.91  144.86    111.120         111.174
2 2008-01-04  143.44  140.91  143.34  141.31    108.397         111.120
3 2008-01-07  142.23  140.10  141.81  141.19    108.305         108.397
4 2008-01-08  142.90  138.44  142.08  138.91    106.556         108.305

C:\Users\q2\Anaconda3\envs\mlp\lib\site-packages\torch\nn\modules\loss.py:446: UserWarning:

Using a target size (torch.Size([])) that is different to the input size (torch.Size([1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.



1599 0 108.50896453857422 105.72000122070312 7.778316497802734
1599 1 107.828857421875 102.88899993896484 24.402191162109375
1599 2 106.96659851074219 102.06099700927734 24.064926147460938
1599 3 106.71932983398438 102.73600006103516 15.866915702819824
1599 4 106.51759338378906 102.07599639892578 19.727783203125
1599 5 106.23387145996094 102.5979995727539 13.219564437866211
1599 6 105.86856842041016 103.54900360107422 5.380381107330322
1599 7 105.45309448242188 104.60800170898438 0.7141817808151245
1599 8 105.0459213256836 103.68699645996094 1.8466768264770508
1599 9 104.58479309082031 103.66400146484375 0.8478572368621826
1599 10 104.12191009521484 103.95600128173828 0.027525734156370163
1599 11 103.68804931640625 104.26200103759766 0.3294205665588379
1599 12 103.33540344238281 103.39600372314453 0.0036723939701914787
1599 13 103.01481628417969 104.03199768066406 1.0346579551696777
1599 14 102.77220916748047 105.34400177001953 6.61411714553833
1599 15 102.67741394042969 106.1340026855

1599 152 97.41117095947266 95.85099792480469 2.4341399669647217
1599 153 97.10040283203125 97.23799896240234 0.01893269456923008
1599 154 96.86858367919922 97.68699645996094 0.6697995066642761
1599 155 96.66937255859375 93.03900146484375 13.179594039916992
1599 156 96.37738800048828 94.59600067138672 3.1733407974243164
1599 157 96.06723022460938 90.34300231933594 32.76678466796875
1599 158 95.67850494384766 93.02300262451172 7.051692485809326
1599 159 95.26255798339844 96.71700286865234 2.1154098510742188
1599 160 94.95547485351562 94.52799987792969 0.18273486196994781
1599 161 94.68992614746094 92.37699890136719 5.349632263183594
1599 162 94.44345092773438 92.6729965209961 3.1345088481903076
1599 163 94.20158386230469 94.12300109863281 0.006175250746309757
1599 164 93.98883819580078 94.16899871826172 0.03245781362056732
1599 165 93.82618713378906 86.79000091552734 49.50791549682617
1599 166 93.6159896850586 90.38200378417969 10.458664894104004
1599 167 93.42109680175781 90.43699645996

1599 299 61.99230194091797 67.90599822998047 34.971805572509766
1599 300 62.762123107910156 66.73500061035156 15.7837553024292
1599 301 63.60527420043945 67.447998046875 14.766526222229004
1599 302 64.18069458007812 68.43599700927734 18.10759925842285
1599 303 65.41929626464844 68.8949966430664 12.080492973327637
1599 304 64.9934310913086 66.00800323486328 1.029356598854065
1599 305 66.78648376464844 67.2969970703125 0.26062384247779846
1599 306 65.97229766845703 66.88600158691406 0.8348548412322998
1599 307 67.22564697265625 67.54199981689453 0.10007911920547485
1599 308 67.08016967773438 68.56300354003906 2.198796272277832
1599 309 67.54655456542969 67.91400146484375 0.13501723110675812
1599 310 67.7620849609375 67.70099639892578 0.0037318123504519463
1599 311 67.9726333618164 69.14099884033203 1.3650778532028198
1599 312 68.18736267089844 69.16400146484375 0.9538233280181885
1599 313 68.37313842773438 69.53600311279297 1.3522542715072632
1599 314 68.53673553466797 71.9020004272461 1

1599 449 82.89639282226562 87.16200256347656 18.19542694091797
1599 450 82.95642852783203 87.63400268554688 21.87969970703125
1599 451 83.02070617675781 88.90499877929688 34.624900817871094
1599 452 83.08869934082031 89.00900268554688 35.049991607666016
1599 453 83.16184997558594 88.9530029296875 33.537452697753906
1599 454 83.23472595214844 87.79399871826172 20.786968231201172
1599 455 83.30860137939453 87.48200225830078 17.417274475097656
1599 456 83.38041687011719 88.59300231933594 27.17104721069336
1599 457 83.45907592773438 88.72899627685547 27.77206039428711
1599 458 83.54396057128906 89.04100036621094 30.21744728088379
1599 459 83.62503051757812 87.59400177001953 15.75273323059082
1599 460 83.71092987060547 87.88999938964844 17.464622497558594
1599 461 83.79347229003906 88.97699737548828 26.868932723999023
1599 462 83.87843322753906 88.93699645996094 25.589061737060547
1599 463 83.96597290039062 88.24099731445312 18.275833129882812
1599 464 84.0596923828125 88.74500274658203 21.

In [35]:
trace1 = {
    'x': np.array(results)[:,0],
    'y': np.array(results)[:,1],

    'type': 'scatter',
#    'name': 'Training',
    'showlegend': False
}

data = [trace1]
        
layout = go.Layout({
    'title': {
        'text': 'Prediction (blue) vs actual (red)',
        'font': {
            'size': 20
        }
    }
})

fig = go.Figure(trace1, layout)
fig.add_trace(go.Scatter(x=np.array(results)[:,0], y=np.array(results)[:,2]))
fig.show()


In [43]:
# Let's generate the SPY validation set

df = valid_asset_dict['SPY']
# df = train_asset_dict['SPY']

display(df.head(5))

train_window = 22
valid_seq, valid_labels = create_input_sequences_from_df(df, train_window)
# print(train_inout_seq)

# Convert our list of lists to Tensors
valid_seq = torch.FloatTensor(valid_seq)
valid_labels = torch.FloatTensor(valid_labels)

print(valid_seq.shape)
print(valid_labels.shape)

# Print first couple of entries to check 
print(valid_seq[0])
print(valid_labels[0])

print(valid_seq[1])
print(valid_labels[1])

Date    High     Low    Open   Close  Adj Close  Prev Adj Close
0 2008-01-02  146.99  143.88  146.53  144.93    111.174         112.156
1 2008-01-03  145.49  144.07  144.91  144.86    111.120         111.174
2 2008-01-04  143.44  140.91  143.34  141.31    108.397         111.120
3 2008-01-07  142.23  140.10  141.81  141.19    108.305         108.397
4 2008-01-08  142.90  138.44  142.08  138.91    106.556         108.305

torch.Size([483, 22, 6])
torch.Size([483])
tensor([[146.5300, 143.8800, 146.9900, 144.9300, 111.1740, 112.1560],
        [144.9100, 144.0700, 145.4900, 144.8600, 111.1200, 111.1740],
        [143.3400, 140.9100, 143.4400, 141.3100, 108.3970, 111.1200],
        [141.8100, 140.1000, 142.2300, 141.1900, 108.3050, 108.3970],
        [142.0800, 138.4400, 142.9000, 138.9100, 106.5560, 108.3050],
        [139.0900, 137.7000, 140.7900, 140.3700, 107.6760, 106.5560],
        [139.6800, 139.3700, 142.8000, 141.2900, 108.3820, 107.6760],
        [140.7800, 139.0000, 141.9000, 140.1500, 107.5070, 108.3820],
        [141.1600, 140.4000, 141.8600, 141.2800, 108.3740, 107.5070],
        [139.7900, 137.9000, 141.4900, 138.1700, 105.9880, 108.3740],
        [137.3600, 136.2800, 139.1200, 136.9800, 105.0760, 105.9880],
        [137.8100, 132.9300, 137.8800, 133.4300, 102.3520, 105.0760],
        [134.7400, 131.1000, 135.0200, 132.0600, 101.3020, 102.3520],
        [127.2100, 126.0000, 132.4300, 130.7200

In [44]:
h = model.init_hidden(batch_size)
    
# Iterate through each of the training samples (seq_len x features)
for j in range(len(valid_labels)):

        # At begining of each training samples we zero out the hidden and cell states
        # This seems a bit odd to me. In the Floydhub example,the hidden / cell states are reset at the 
        # beginning of each epoch.
        # Hidden and cell state dimensions should be num layers x batch size x hidden layer size
            
        # This is needed inside the sequence loop for back propagation to work
    h = tuple(e.data for e in h)

        # Send input / label data to Cuda if available
    inputs = valid_seq[j].to(device)
    labels = valid_labels[j].to(device)
        
    optimizer.zero_grad()
            
    y_pred, h = model(inputs, h)
       
    train_loss = loss_function(y_pred, labels)
 
        # Printing out the training loss etc during one of the later epoch's reveals that even when the eventual
        # epoch loss is close to zero, at the start of each epoch the loss is quite high. It gets down to zero
        # perhaps after 200 or so of the training samples. So, even with a trained network, you need to train the 
        # LSTM with a sequence of training samples to get the loss down first. I think this must be what folks
        # refer to as "warming up" the network.

    print(i, j, y_pred[0].item(), labels.item(), train_loss.item())
               
    train_loss.backward()
    optimizer.step()
        
    # Measure the validation loss
valid_loss = 0
    

print('Epoch:{:3}'.format(i), '\tTrain Loss:{:1.3f}'.format(train_loss.item()), '\tValid Loss:{:1.3f}'.format(valid_loss))


C:\Users\q2\Anaconda3\envs\mlp\lib\site-packages\torch\nn\modules\loss.py:446: UserWarning:

Using a target size (torch.Size([])) that is different to the input size (torch.Size([1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.



9 0 110.94184875488281 105.72000122070312 27.26769256591797
9 1 110.9524154663086 102.88899993896484 65.01866912841797
9 2 110.95587158203125 102.06099700927734 79.1187973022461
9 3 110.95231628417969 102.73600006103516 67.50785064697266
9 4 110.94292449951172 102.07599639892578 78.6224136352539
9 5 110.92781066894531 102.5979995727539 69.38574981689453
9 6 110.9079360961914 103.54900360107422 54.15388870239258
9 7 110.88453674316406 104.60800170898438 39.394893646240234
9 8 110.85873413085938 103.68699645996094 51.43382263183594
9 9 110.83011627197266 103.66400146484375 51.35320281982422
9 10 110.79898071289062 103.95600128173828 46.82636642456055
9 11 110.76578521728516 104.26200103759766 42.29920959472656
9 12 110.73103332519531 103.39600372314453 53.80265808105469
9 13 110.6942138671875 104.03199768066406 44.38512420654297
9 14 110.65606689453125 105.34400177001953 28.218036651611328
9 15 110.6176986694336 106.13400268554688 20.10352897644043
9 16 110.57980346679688 106.02700042724

9 157 104.64350128173828 90.34300231933594 204.5042724609375
9 158 104.5770263671875 93.02300262451172 133.49546813964844
9 159 104.50831604003906 96.71700286865234 60.704559326171875
9 160 104.44043731689453 94.52799987792969 98.25641632080078
9 161 104.37171936035156 92.37699890136719 143.87332153320312
9 162 104.3006362915039 92.6729965209961 135.20201110839844
9 163 104.22773742675781 94.12300109863281 102.10569763183594
9 164 104.15435791015625 94.16899871826172 99.7073974609375
9 165 104.08064270019531 86.79000091552734 298.9662780761719
9 166 104.00106048583984 90.38200378417969 185.47869873046875
9 167 103.9190673828125 90.43699645996094 181.7662353515625
9 168 103.83494567871094 87.15599822998047 278.1872863769531
9 169 103.7465591430664 85.9800033569336 315.6505126953125
9 170 103.6535415649414 81.5999984741211 486.3587646484375
9 171 103.55322265625 77.94599914550781 655.7299194335938
9 172 103.44379425048828 75.98200225830078 754.1500244140625
9 173 103.32500457763672 70.67

9 317 68.78087615966797 71.88600158691406 9.641803741455078
9 318 69.22736358642578 73.56300354003906 18.797773361206055
9 319 69.7645034790039 72.18699645996094 5.868472099304199
9 320 70.32787322998047 71.9729995727539 2.7064406871795654
9 321 70.8909912109375 70.16100311279297 0.5328826308250427
9 322 71.37627410888672 70.76300048828125 0.37610453367233276
9 323 71.7926025390625 70.18499755859375 2.5843937397003174
9 324 72.11164093017578 72.17900085449219 0.004537359345704317
9 325 72.4005355834961 72.09200286865234 0.09519243240356445
9 326 72.6484375 71.60900115966797 1.080427885055542
9 327 72.83564758300781 70.58100128173828 5.08342981338501
9 328 72.92546081542969 70.43000030517578 6.227323055267334
9 329 72.92256927490234 72.23400115966797 0.47412604093551636
9 330 72.89710998535156 70.94499969482422 3.810734510421753
9 331 72.80972290039062 71.93299865722656 0.7686454057693481
9 332 72.70252227783203 73.20700073242188 0.25449851155281067
9 333 72.62287139892578 74.9800033569

9 476 86.51018524169922 89.8010025024414 10.82947826385498
9 477 86.60025024414062 89.97799682617188 11.409172058105469
9 478 86.68928527832031 90.40399932861328 13.799100875854492
9 479 86.7759017944336 90.59700012207031 14.60079288482666
9 480 86.85774230957031 90.46900177001953 13.041194915771484
9 481 86.9331283569336 90.43599700927734 12.270089149475098
9 482 87.00115966796875 89.56800079345703 6.5886735916137695
Epoch:  9 	Train Loss:6.589 	Valid Loss:0.000


In [28]:
batch_size = 1

model.train()

valid_loss_vs_seq = []
for j in range(len(valid_labels)):
    
    h = model.init_hidden(batch_size)
          
    # This is needed inside the sequence loop for back propagation to work
#    h = tuple(e.data for e in h)

    # Send input / label data to Cuda if available
    inputs = valid_seq[j].to(device)
    labels = valid_labels[j].to(device)
        
    y_pred, h = model(inputs, h)
        
    single_loss = loss_function(y_pred, labels)
    print(j, y_pred[0].item(), labels.item(), single_loss.item())    
    
    valid_loss_vs_seq.append((j, single_loss))
    


C:\Users\q2\Anaconda3\envs\mlp\lib\site-packages\torch\nn\modules\loss.py:446: UserWarning:

Using a target size (torch.Size([])) that is different to the input size (torch.Size([1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.



0 -2.447566270828247 86.447998046875 7902.4208984375
1 -2.4485390186309814 87.37100219726562 8067.55029296875
2 -2.4475672245025635 87.25399780273438 8046.37158203125
3 -2.448539972305298 87.35600280761719 8064.85595703125
4 -2.447566270828247 86.7020034790039 7947.64501953125
5 -2.447566270828247 87.01499938964844 8003.55029296875
6 -2.4475653171539307 87.76300048828125 8137.94580078125
7 -2.4475653171539307 87.697998046875 8126.22216796875
8 -2.4485390186309814 88.0250015258789 8185.46142578125
9 -2.448538064956665 88.08300018310547 8195.9599609375
10 -2.4475643634796143 87.37100219726562 8067.37451171875
11 -2.4485371112823486 87.48699951171875 8088.4013671875
12 -2.4475624561309814 86.18599700927734 7855.908203125
13 -2.4485361576080322 86.80400085449219 7966.01611328125
14 -2.4485361576080322 87.37799835205078 8068.80712890625
15 -2.447561502456665 88.24299621582031 8224.77734375
16 -2.4485361576080322 87.66100311279297 8119.7294921875
17 -2.448535203933716 88.09700012207031 8198.

177 -2.448530435562134 87.61900329589844 8112.1611328125
178 -2.44853138923645 86.66999816894531 7942.1123046875
179 -2.4485347270965576 88.11199951171875 8201.2099609375
180 -2.448535203933716 86.55999755859375 7922.5185546875
181 -2.448535680770874 86.89800262451172 7982.80322265625
182 -2.4485361576080322 88.24400329589844 8225.1376953125
183 -2.4485361576080322 88.06800079345703 8193.244140625
184 -2.4485361576080322 87.80999755859375 8146.603515625
185 -2.4485371112823486 86.8759994506836 7978.87353515625
186 -2.448538064956665 88.12699890136719 8203.927734375
187 -2.4475643634796143 88.36900329589844 8247.6484375
188 -2.447563409805298 88.63400268554688 8295.8515625
189 -2.4475643634796143 89.56099700927734 8465.5751953125
190 -2.4475643634796143 89.94300079345703 8536.0166015625
191 -2.448538064956665 89.82599639892578 8514.58984375
192 -2.4485390186309814 89.91400146484375 8530.8388671875
193 -2.4475653171539307 89.91400146484375 8530.658203125
194 -2.4485371112823486 90.031997

358 -2.448521852493286 94.41799926757812 9383.123046875
359 -2.448521852493286 94.59700012207031 9417.833984375
360 -2.448521852493286 95.01399993896484 9498.943359375
361 -2.4485208988189697 94.0 9302.318359375
362 -2.448521852493286 92.47100067138672 9009.7158203125
363 -2.448521852493286 92.11299896240234 8941.8818359375
364 -2.4485208988189697 91.97899627685547 8916.556640625
365 -2.448518991470337 92.4489974975586 9005.5380859375
366 -2.4485185146331787 93.73100280761719 9250.5
367 -2.448518991470337 93.08999633789062 9127.607421875
368 -2.448521852493286 92.43399810791016 9002.693359375
369 -2.448521852493286 94.11900329589844 9325.287109375
370 -2.4485185146331787 94.45500183105469 9390.2919921875
371 -2.4485208988189697 94.58200073242188 9414.9228515625
372 -2.4485208988189697 94.49199676513672 9397.46484375
373 -2.4485180377960205 95.43900299072266 9581.966796875
374 -2.4485199451446533 95.34200286865234 9562.9853515625
375 -2.448517084121704 94.87200164794922 9471.283203125
3

542 -2.4484989643096924 107.49800109863281 12088.2333984375
543 -2.449159860610962 108.65499877929688 12344.1337890625
544 -2.4484989643096924 108.7760009765625 12370.8896484375
545 -2.4484989643096924 109.07099914550781 12436.5986328125
546 -2.4484989643096924 109.22200012207031 12470.30078125
547 -2.4484989643096924 109.35099792480469 12499.1279296875
548 -2.4485013484954834 108.90399932861328 12399.3798828125
549 -2.4484989643096924 109.38800048828125 12507.4033203125
550 -2.4484989643096924 109.88700103759766 12619.265625
551 -2.4484989643096924 110.93099975585938 12854.9111328125
552 -2.4484989643096924 111.22599792480469 12921.8916015625
553 -2.448498010635376 111.36199951171875 12952.830078125
554 -2.448500871658325 111.33200073242188 12946.0029296875
555 -2.4484989643096924 112.38300323486328 13186.2744140625
556 -2.448498010635376 111.95899963378906 13089.076171875
557 -2.4484970569610596 112.00499725341797 13099.6015625
558 -2.4484970569610596 113.03299713134766 13335.9746093

722 -2.4484970569610596 110.69400024414062 12801.2236328125
723 -2.4484970569610596 111.31199645996094 12941.44921875
724 -2.4484970569610596 111.31199645996094 12941.44921875
725 -2.448496103286743 112.01399993896484 13101.662109375
726 -2.4484970569610596 113.62899780273438 13473.984375
727 -2.4491560459136963 114.47200012207031 13670.5576171875
728 -2.4484989643096924 114.71800231933594 13727.9892578125
729 -2.4484989643096924 113.2760009765625 13392.16015625
730 -2.4491560459136963 112.99199676513672 13326.66015625
731 -2.4491560459136963 112.15599822998047 13134.341796875


In [96]:
print(valid_loss_vs_seq)

[(0, tensor(116.6719, device='cuda:0', grad_fn=<MseLossBackward>)), (1, tensor(135.2448, device='cuda:0', grad_fn=<MseLossBackward>)), (2, tensor(120.0005, device='cuda:0', grad_fn=<MseLossBackward>)), (3, tensor(134.8961, device='cuda:0', grad_fn=<MseLossBackward>)), (4, tensor(123.0430, device='cuda:0', grad_fn=<MseLossBackward>)), (5, tensor(102.8494, device='cuda:0', grad_fn=<MseLossBackward>)), (6, tensor(82.4913, device='cuda:0', grad_fn=<MseLossBackward>)), (7, tensor(100.0696, device='cuda:0', grad_fn=<MseLossBackward>)), (8, tensor(100.5302, device='cuda:0', grad_fn=<MseLossBackward>)), (9, tensor(94.7600, device='cuda:0', grad_fn=<MseLossBackward>)), (10, tensor(88.8961, device='cuda:0', grad_fn=<MseLossBackward>)), (11, tensor(105.9762, device='cuda:0', grad_fn=<MseLossBackward>)), (12, tensor(93.2862, device='cuda:0', grad_fn=<MseLossBackward>)), (13, tensor(69.6636, device='cuda:0', grad_fn=<MseLossBackward>)), (14, tensor(57.1003, device='cuda:0', grad_fn=<MseLossBackward